Code from https://gitlab.com/mrcagney/gtfs_kit/-/blob/master/notebooks/examples.ipynb

Note: created env_gtfs-kit.yml environment to test the package `gtfs_kit`

In [1]:
import sys
from pathlib import Path
import json

import pandas as pd
import numpy as np
import geopandas as gp
import matplotlib

# DIR = Path('..')
# sys.path.append(str(DIR))

import gtfs_kit as gk

# DATA_DIR = DIR/'data/'

%load_ext autoreload
%autoreload 2
%matplotlib inline

In [8]:
# paths definition

home_folder = '/Users/azanchetta/OneDrive - The Alan Turing Institute/demoland_data/raw/GTFS'
itm_all_filename = 'itm_all_gtfs.zip'
NE_filename = 'NE.zip'

path_to_itm = f"{home_folder}/{itm_all_filename}"
path_to_NE = f"{home_folder}/{NE_filename}"

In [19]:
# List feed

gk.list_feed(path_to_itm)

file_name   file_size
0          agency.txt       76812
1        calendar.txt      379778
2  calendar_dates.txt     4448876
3       feed_info.txt         164
4     frequencies.txt        1272
5          routes.txt      292606
6          shapes.txt  1447549654
7      stop_times.txt  3283551074
8           stops.txt    19932823
9           trips.txt   105135612

In [28]:
 # Read feed and describe
feed = gk.read_feed(path_to_itm,
                    dist_units='km')
feed.describe()

/usr/local/anaconda3/envs/gtfskit_env/lib/python3.9/site-packages/gtfs_kit/feed.py:465: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(p, dtype=cs.DTYPE, encoding="utf-8-sig")
/usr/local/anaconda3/envs/gtfskit_env/lib/python3.9/site-packages/gtfs_kit/feed.py:465: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(p, dtype=cs.DTYPE, encoding="utf-8-sig")


indicator  \
0                           agencies   
1                           timezone   
2                         start_date   
3                           end_date   
4                         num_routes   
5                          num_trips   
6                          num_stops   
7                         num_shapes   
8                        sample_date   
9   num_routes_active_on_sample_date   
10   num_trips_active_on_sample_date   
11   num_stops_active_on_sample_date   

                                                value  
0   [Cardiff Bus, Dilwyn's Coaches, O R Jones, P &...  
1                                       Europe/London  
2                                            20230103  
3                                            20231020  
4                                               13148  
5                                              891514  
6                                              313128  
7                                               21109  
8                                            20230112  
9                                                   0  
10                                                  0  
11                                                  0

In [12]:
 # Validate

# feed.validate()
#  not running yet, as I had check already by command line with FeedValidator, and I think might take long to run

In [ ]:
display(feed.stop_times.head().T)

# feed = feed.append_dist_to_stop_times()
# feed.stop_times.head().T

In [23]:
 # Choose study dates

week = feed.get_first_week()
dates = [week[4], week[6]]  # First Friday and Sunday
dates

['20230113', '20230115']

In [ ]:
# Compute feed time series

trip_stats = feed.compute_trip_stats()
trip_stats.head().T
fts = feed.compute_feed_time_series(trip_stats, dates, freq='6H')
fts

In [ ]:
# Compute route time series

rts = feed.compute_route_time_series(trip_stats, dates, freq='12H')
rts 


In [40]:
# Map routes
rid = ['50425']

feed.routes.head()
# feed.map_routes(rid)

geojson_file = feed.routes_to_geojson()

/usr/local/anaconda3/envs/gtfskit_env/lib/python3.9/site-packages/pandas/core/dtypes/cast.py:127: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)
/usr/local/anaconda3/envs/gtfskit_env/lib/python3.9/site-packages/pandas/core/dtypes/cast.py:127: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)
/usr/local/anaconda3/envs/gtfskit_env/lib/python3.9/site-packages/pandas/core/dtypes/cast.py:127: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  arr = construct_1d_object_array_from_listlike(values)
/usr/local/anaconda3/envs/gtfskit_env/lib/python3.9/site-packages/pandas/core/dtypes/cast.p

In [43]:
with open('trials_routes_itm_frompython.geojson', 'w', encoding='utf-8') as f:
    json.dump(geojson_file, f, ensure_ascii=False)

In [45]:
with open('trial_jsontocsv.csv', 'w') as f:  # You will need 'wb' mode in Python 2.x
    w = csv.DictWriter(f, geojson_file.keys())
    w.writeheader()
    w.writerow(geojson_file)

NameError: name 'csv' is not defined